In [1]:
# Query information about the used Julia installation.
versioninfo()

Julia Version 1.5.0
Commit 96786e22cc (2020-08-01 23:44 UTC)
Platform Info:
  OS: Linux (x86_64-pc-linux-gnu)
  CPU: Intel(R) Xeon(R) CPU E5-2690 v3 @ 2.60GHz
  WORD_SIZE: 64
  LIBM: libopenlibm
  LLVM: libLLVM-9.0.1 (ORCJIT, haswell)
Environment:
  EBJULIA_USER_DEPOT_PATH = /users/omlins/.julia/1.5.0/daint-gpu
  JULIA_DEPOT_PATH = /apps/daint/UES/jenkins/7.0.UP01/gpu/easybuild/software/jupyterlab/1.2.16-CrayGNU-19.10-cuda-10.1-batchspawner/share/IJulia:/apps/daint/UES/jenkins/7.0.UP01/gpu/easybuild/software/JuliaExtensions/1.5.0-CrayGNU-19.10-cuda-10.1/extensions:/users/omlins/.julia/1.5.0/daint-gpu:/apps/daint/UES/jenkins/7.0.UP01/gpu/easybuild/software/Julia/1.5.0-CrayGNU-19.10-cuda-10.1/extensions:/apps/daint/UES/jenkins/7.0.UP01/gpu/easybuild/software/Julia/1.5.0-CrayGNU-19.10-cuda-10.1/local/share/julia:/apps/daint/UES/jenkins/7.0.UP01/gpu/easybuild/software/Julia/1.5.0-CrayGNU-19.10-cuda-10.1/share/julia
  JULIA_CUDA_USE_BINARYBUILDER = false
  EBJULIA_ENV_NAME = 1.5.0-daint-gpu

In [2]:
# Check additional installed packages.
using Pkg
Pkg.status()

Status `~/.julia/1.5.0/daint-gpu/environments/1.5.0-daint-gpu/Project.toml` (empty project)


In [3]:
# Add a package...
Pkg.add("TickTock")

  Resolving package versions...
  Installed TickTock ─ v1.0.0
Updating `~/.julia/1.5.0/daint-gpu/environments/1.5.0-daint-gpu/Project.toml`
  [9ff05d80] + TickTock v1.0.0
Updating `~/.julia/1.5.0/daint-gpu/environments/1.5.0-daint-gpu/Manifest.toml`
  [9ff05d80] + TickTock v1.0.0
  [2a0f44e3] + Base64
  [ade2ca70] + Dates
  [8ba89e20] + Distributed
  [b77e0a4c] + InteractiveUtils
  [76f85450] + LibGit2
  [8f399da3] + Libdl
  [56ddb016] + Logging
  [d6f4376e] + Markdown
  [44cfe95a] + Pkg
  [de0858da] + Printf
  [3fa0cd96] + REPL
  [9a3f8284] + Random
  [ea8e919c] + SHA
  [9e88b42a] + Serialization
  [6462fe0b] + Sockets
  [8dfed614] + Test
  [cf7118a7] + UUIDs
  [4ec0a83e] + Unicode


In [4]:
#... and check Pkg status again.
Pkg.status()

Status `~/.julia/1.5.0/daint-gpu/environments/1.5.0-daint-gpu/Project.toml`
  [9ff05d80] TickTock v1.0.0


In [5]:
# Remove the package again...
Pkg.rm("TickTock")

Updating `~/.julia/1.5.0/daint-gpu/environments/1.5.0-daint-gpu/Project.toml`
  [9ff05d80] - TickTock v1.0.0
Updating `~/.julia/1.5.0/daint-gpu/environments/1.5.0-daint-gpu/Manifest.toml`
  [9ff05d80] - TickTock v1.0.0
  [2a0f44e3] - Base64
  [ade2ca70] - Dates
  [8ba89e20] - Distributed
  [b77e0a4c] - InteractiveUtils
  [76f85450] - LibGit2
  [8f399da3] - Libdl
  [56ddb016] - Logging
  [d6f4376e] - Markdown
  [44cfe95a] - Pkg
  [de0858da] - Printf
  [3fa0cd96] - REPL
  [9a3f8284] - Random
  [ea8e919c] - SHA
  [9e88b42a] - Serialization
  [6462fe0b] - Sockets
  [8dfed614] - Test
  [cf7118a7] - UUIDs
  [4ec0a83e] - Unicode


In [6]:
#... and check Pkg status again.
Pkg.status()

Status `~/.julia/1.5.0/daint-gpu/environments/1.5.0-daint-gpu/Project.toml` (empty project)


In [7]:
# Use CUDA to access the GPU (the first calls take a while as it does some pre-compilation!).
using CUDA

┌ Info: Precompiling CUDA [052768ef-5323-5732-b1bb-66c8b64840ba]
└ @ Base loading.jl:1278


In [8]:
# Do some simple computations on the GPU using Array broadcasting (the first calls take a while as it does some pre-compilation!).
A = CUDA.ones(2,2)
B = CUDA.ones(2,2)
C = A .+ 3*B

2×2 CuArray{Float32,2}:
 4.0  4.0
 4.0  4.0

In [9]:
# Do some simple computations on the GPU using Julia native kernel programming.
A = CUDA.zeros(2,2)
B = CUDA.ones(2,2)

function f(X, Y)
	ix = (blockIdx().x-1) * blockDim().x + threadIdx().x
	iy = (blockIdx().y-1) * blockDim().y + threadIdx().y
	X[ix,iy] = 2*Y[ix,iy]
	return
end

@cuda threads=(2,2) f(A, B)
A

2×2 CuArray{Float32,2}:
 2.0  2.0
 2.0  2.0